# Sistema de Compressão

$ \frac{d\dot{m}}{dt} = \frac{A_1}{L_C}(\phi (N(t), \dot{m})P_1 - P_P(t)) $

$ \frac{d P_P}{dt} = \frac{C_1^2}{\nu _P}(\dot{m}(t) - \alpha (t) K_\nu \sqrt{P_P - P_{out}}) $

$ \begin{matrix} A_1 & = & 2.6\centerdot 10^{-3} m² \\
\nu _P & = & 2.0 m³ \\
L_C & = & 2.0 m \\
K_\nu & = & \frac{0.38 kg}{(kPa)^{0.5}s} \\
P_1 & = & 4.5 MPa \\
P{out} & = & 5.0 MPa \end{matrix}
$

$ \frac{d\dot{m}}{dt} = \frac{2.6\centerdot 10^{-3}}{2.0}(1.5\centerdot 4.5 - P_P) $

$ \frac{d P_P}{dt} = \frac{479.029^2}{2.0}(\dot{m} - \alpha {0.38} \sqrt{P_P - 5.0}) $

#### Importações

In [1]:
import numpy as np
from scipy.optimize import fsolve
import casadi as ca
import plotly.graph_objects as go
import optuna
from plotly.subplots import make_subplots
import time
import torch
import torch.nn as nn
import torch.optim as optim
from torch.utils.data import DataLoader, TensorDataset

from libs.numSol import Simulation
from libs.Model import MyModel


/home/matheusmarinho/.local/lib/python3.10/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


#### Constantes e Variáveis Auxiliares

In [2]:
np.random.seed(42)
print(np.random.seed)

# Constantes
A1 = (2.6)*(10**-3)
Lc = 2
kv = 0.38
P1 = 4.5
P_out = 5
C = 479

timestep = 3 # Passos no passado para prever o próximo
epochs = 5000
nData = 3000 
nAlphas = 5 # Número de vezes que o Alfa irá mudar, considere o treino e os testes.
alphas = np.random.uniform(0.35,0.65, nAlphas+1) # Abertura da válvula
perturb = 1e-4
tempo = 300
dt = 0.1 # Tempo amostral

# Variáveis auxiliares
interval = [np.linspace(i * tempo, (i + 1) * tempo, nData) for i in range(nAlphas)]
interval_test = [np.linspace(i * 500, (i + 1) * 500, 5000) for i in range(nAlphas)]
massFlowrate = []
PlenumPressure = []
alpha_values = []
RNN_train = []
RNN_trainFut = []

<built-in function seed>


### Solução Numérica

##### Cálculo da Solução

In [3]:
# Crie uma instância da classe Simulation
sim = Simulation(A1, Lc, kv, P1, P_out, C, alphas, nAlphas, nData, perturb, tempo, dt)

# Execute a simulação
sim.run()

RNN_train = sim.RNN_train
RNN_trainFut = sim.RNN_trainFut
massFlowrate = sim.massFlowrate
PlenumPressure = sim.PlenumPressure
alpha_values = sim.alpha_values


##### Gráfico do Modelo

In [4]:
fig = make_subplots(rows=1, cols=3, subplot_titles=("Vazão vs Tempo", "Pressão vs Tempo", "Alpha vs Tempo"))

for i in range(0, nAlphas):
    # Vazão
    fig.add_trace(go.Scatter(x=interval[i], y=np.squeeze(massFlowrate[i]), mode='lines',
                             name='Vazão', legendgroup='massflow', showlegend=i == 0), row = 1, col = 1)
    # Pressão
    fig.add_trace(go.Scatter(x=interval[i], y=np.squeeze(PlenumPressure[i]), mode='lines',
                             name='Pressão', legendgroup='pressure', showlegend=i == 0), row = 1, col = 2)
    # Alphas
    fig.add_trace(go.Scatter(x=interval[i], y=np.squeeze(alpha_values[i]), mode='lines', 
                             name='Alphas', line=dict(dash='dash'), legendgroup='alpha', showlegend=i == 0), row = 1, col = 3)

# Atualiza layout
fig.update_layout(
    xaxis_title='Tempo',
    grid=dict(rows=1, columns=3),
    template='plotly',
    showlegend=False
)

# Mostra a figura
fig.show()


### Rede Neural

##### Dados de Treino

In [5]:
RNN_train = np.array(RNN_train)


X_train = []
y_train = []

for i in range(len(RNN_train) - timestep):
    X_train.append(RNN_train[i:i + timestep])  
    if i + timestep < len(RNN_train):           
        y_train.append(RNN_train[i + timestep, :2])  

X_train = torch.tensor(X_train, dtype=torch.float32)
y_train = torch.tensor(y_train, dtype=torch.float32)

x_min = X_train.amin(dim=(0, 1), keepdim=True)
x_max = X_train.amax(dim=(0, 1), keepdim=True)
print(x_min.shape)

y_train = y_train.unsqueeze(1)

torch.Size([1, 1, 3])


/tmp/ipykernel_8517/2752278696.py:12: UserWarning:

Creating a tensor from a list of numpy.ndarrays is extremely slow. Please consider converting the list to a single numpy.ndarray with numpy.array() before converting to a tensor. (Triggered internally at ../torch/csrc/utils/tensor_new.cpp:278.)



##### Rede

##### Treinamento

In [6]:
# def objective(trial):
#     lr = trial.suggest_float('lr', 1e-6, 1e-3, log=True) 
#     units = trial.suggest_int('units', 32, 64)
#     batch_size = trial.suggest_int('batch_size', 16, 64) 
#     num_layers = trial.suggest_int('num_layers', 0, 5)  

#     model = create_model(lr, num_layers, units)

#     model.fit(X_train, y_train, epochs=250, batch_size=batch_size, verbose=0)

#     # Avaliação
#     loss = model.evaluate(X_train, y_train, verbose=0)
#     return loss

# study = optuna.create_study(direction='minimize')
# study.optimize(objective, n_trials=5)  # Ajuste o número de tentativas conforme necessário

# # Exibir os melhores hiperparâmetros
# print("Melhores hiperparâmetros: ", study.best_params)

In [7]:
model = MyModel(20, A1, Lc, kv, P1, P_out, C, dt, x_min, x_max)

train_dataset = TensorDataset(X_train, y_train)
train_loader_Adam = DataLoader(train_dataset, batch_size= 32 , shuffle=True)
train_loader_LBFGS = DataLoader(train_dataset)
Adam = optim.Adam
model.train_model(model, train_loader_Adam, 1e-5, 20, Adam)

Epoch [1/20], Loss: 4.006604529647176
Epoch [2/20], Loss: 3.693074112762012
Epoch [3/20], Loss: 3.394319560227872
Epoch [4/20], Loss: 3.1052524713056684
Epoch [5/20], Loss: 2.8235785892523175
Epoch [6/20], Loss: 2.5489462021825666
Epoch [7/20], Loss: 2.2832874562948753
Epoch [8/20], Loss: 2.0315663290938843
Epoch [9/20], Loss: 1.7985443169120023
Epoch [10/20], Loss: 1.5857450352040434
Epoch [11/20], Loss: 1.395943056037431
Epoch [12/20], Loss: 1.2275833830650427
Epoch [13/20], Loss: 1.0802537606977451
Epoch [14/20], Loss: 0.9499592319734569
Epoch [15/20], Loss: 0.8340002401297026
Epoch [16/20], Loss: 0.7309069240779511
Epoch [17/20], Loss: 0.6375972153281352
Epoch [18/20], Loss: 0.5525214181525875
Epoch [19/20], Loss: 0.4738015639565901
Epoch [20/20], Loss: 0.4002689534921382


##### Dados de teste

In [8]:
massFlowrateTeste = []
PlenumPressureTeste = []
RNN_test = []
x_test = []
alpha_valuesTeste = []
aux1 = []
aux2 = []
alphasTeste = np.random.uniform(0.35,0.65, nAlphas) # Abertura da válvula
interval3 = np.linspace(0, 2500, 24997)
sim = Simulation(A1, Lc, kv, P1, P_out, C, alphasTeste, nAlphas, 5000, perturb, tempo, dt)

sim.run()

RNN_test = sim.RNN_train
massFlowrateTeste = sim.massFlowrate
PlenumPressureTeste = sim.PlenumPressure
alpha_valuesTeste = sim.alpha_values
time2 = sim.time

RNN_test = np.array(RNN_test)

for i in range(len(RNN_test) - 3):
    x_test.append(RNN_test[i:i + 3])

x_test = torch.tensor(x_test, dtype=torch.float32)

massFlowrateTeste = np.array(massFlowrateTeste)
PlenumPressureTeste = np.array(PlenumPressureTeste)
print(time2)

5.083230257034302


##### Gráfico Rede Neural

In [12]:
massFlowrate100, PlenumPressure100, timeteste = model.test_model(x_test, interval3, model)
print(f"Tempo total: {timeteste} segundos")

Tempo total: 4.056582689285278 segundos


In [10]:
fig3 = make_subplots(rows=1, cols=3, subplot_titles=("Loss","Mass Flow Rate vs Time", "Plenum Pressure vs Time"))

fig3.add_trace(go.Scatter(x=interval3,y=np.squeeze(massFlowrate100),mode='lines',
                                line=dict(dash='solid')),row=1, col=2)
fig3.add_trace(go.Scatter(x=interval3,y=np.squeeze(PlenumPressure100),mode='lines',
                                line=dict(dash='solid')),row=1, col=3)



for i in range(nAlphas):
    # Modelo
    fig3.add_trace(go.Scatter(x=np.squeeze(interval_test[i]), y=np.squeeze(massFlowrateTeste[i]), mode='lines',name='Model Mass Flow Rate', line=dict(dash='dash', color='green')),
                  row=1, col=2)
    fig3.add_trace(go.Scatter(x=np.squeeze(interval_test[i]), y=np.squeeze(PlenumPressureTeste[i]), mode='lines', name= 'Model Plenum Pressure', line=dict(dash='dash', color='green')),
                  row=1, col=3)

fig3.update_layout(
    title='Resultados Rede Neural',
    xaxis_title='Time',
    yaxis_title='Value',
    template='plotly',
    showlegend=False
)
fig3.show()